In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

import scipy 
import scipy as sp

from scipy import stats,signal
import statsmodels.api as sm
import math

from scipy.fft import fft, ifft 

from scipy.signal import medfilt


col = ['X','Y', 'Z']

In [2]:
# import the median filter function
# return the med-filtered signal: numpy array 1D
def median_filter(signal):       # input: numpy array 1D (one column)
    array=np.array(signal) 
    
    #applying the median filter
    med_filtered=scipy.signal.medfilt(array, kernel_size=3) # applying the median filter order3(kernel_size=3)
    return  med_filtered 


## Low-path Butterworth Filter
def butter_lowpass(cutoff, nyq_freq, order): ##CORRECT
    normal_cutoff = float(cutoff) / nyq_freq
    b, a = signal.butter(order, normal_cutoff, btype='lowpass')
    return b, a

def butter_lowpass_filter(data, cutoff_freq, nyq_freq, order): ##CORRECT
    b, a = butter_lowpass(cutoff_freq, nyq_freq, order=order)
    y = signal.filtfilt(b, a, data) 
    return y



## Derivative
def jerk_one_signal(signal):
    dt=0.02 # dt=1/50=0.02s time duration between two rows
    return np.array([(signal[i+1]-signal[i])/dt for i in range(len(signal)-1)])
#     return signal.diff()


### Magnitude
def mag(df):
    result = []
    for i in range(df.shape[0]):
        x, y, z = df.iloc[i,:].values
        mag = np.sqrt(x**2 + y**2 + z**2)
        result.append(mag)
    return result


## FFT
from scipy import fftpack # import fftpack to use all fft functions
from numpy.fft import *

##################### fast_fourier_transform_one_signal #################
# Inputs: time signal 1D array
# Output: amplitude of fft components 1D array having the same lenght as the Input
def fast_fourier_transform_one_signal(t_signal):
    # apply fast fourrier transform to the t_signal
    complex_f_signal= fftpack.fft(t_signal)
    #compute the amplitude each complex number
    amplitude_f_signal=np.abs(complex_f_signal)
    # return the amplitude
    return amplitude_f_signal

In [3]:
#     for i in col:
#         _,_,tBodyGyro[i],_ = components_selection_one_signal(med_gryo[i])
#         _, tGravityAcc[i], tBodyAcc[i],_= components_selection_one_signal(base_ac) 

In [4]:
def main(acc, gryo):
    
    med_gryo = pd.DataFrame(columns=col)
    med_acc = pd.DataFrame(columns=col)
    for i in col:
        med_gryo[i] = median_filter(gryo[i])
        med_acc[i] = median_filter(acc[i])
        
     
    ##############################################################
    #Butterworth Filter
    ##############################################################
    
    sample_rate = 50                    # 50Hz
    signal_length = 2.56 * sample_rate  # 2.56 seconds
    freq_20 = 20.0                      # 20Hz
    freq_03 = 0.3                       # 0.3HZ
    nyq_freq = sample_rate / 2          # 25Hz
    
    
    tGyro = pd.DataFrame(columns=col)
    tAcc = pd.DataFrame(columns=col)

    for i in col:
        tGyro[i] = butter_lowpass_filter(med_gryo[i], freq_20, nyq_freq, 3)
        tAcc[i] = butter_lowpass_filter(med_acc[i], freq_20, nyq_freq, 3)

    tBodyGyro = tGyro

    tGravityAcc = pd.DataFrame(columns=col)
    tBodyAcc = pd.DataFrame(columns=col)

    for i in col:
        tGravityAcc[i] = butter_lowpass_filter(tAcc[i], 0.3, nyq_freq, 1)
        tBodyAcc[i] = tAcc[i] - tGravityAcc[i] 



    
    tBodyAccJerk = pd.DataFrame(columns=col)
    tBodyGyroJerk = pd.DataFrame(columns=col)


    for i in col:
        #Derivative
        tBodyAccJerk[i] = jerk_one_signal(tBodyAcc[i])
        tBodyGyroJerk[i] = jerk_one_signal(tBodyGyro[i])
        
#     tBodyAccJerk.fillna(0, inplace = True)
#     tBodyGyroJerk.fillna(0, inplace = True)
        
    tGravityAcc = tBodyGyro[:-1]
    tBodyAcc = tBodyAcc[:-1]
     
    tBodyGyro = tBodyGyro[:-1]
    
    ##############################################################
    # Magnitude
    ##############################################################
    
    
    tBodyAccMag = pd.DataFrame(columns=['tBodyAccMag'])
    tBodyAccMag['tBodyAccMag'] =  mag(tBodyAcc)

    tGravityAccMag = pd.DataFrame(columns=['tGravityAccMag'])
    tGravityAccMag['tGravityAccMag'] = mag(tGravityAcc)

    tBodyAccJerkMag = pd.DataFrame(columns=['tBodyAccJerkMag'])
    tBodyAccJerkMag['tBodyAccJerkMag'] = mag(tBodyAccJerk)

    tBodyGyroMag = pd.DataFrame(columns=['tBodyGyroMag'])
    tBodyGyroMag['tBodyGyroMag'] = mag(tBodyGyro)

    tBodyGyroJerkMag = pd.DataFrame(columns=['tBodyGyroJerkMag'])
    tBodyGyroJerkMag['tBodyGyroJerkMag'] = mag(tBodyGyroJerk)
    
    
    ##############################################################
    # Fourier Transform
    ##############################################################
    
    fBodyAcc= pd.DataFrame(columns=col)
    fBodyAccJerk = pd.DataFrame(columns=col)
    fBodyGyro = pd.DataFrame(columns=col)

    for i in col:
        fBodyAcc[i] = fast_fourier_transform_one_signal(tBodyAcc[i].values)
        fBodyAccJerk[i] = fast_fourier_transform_one_signal(tBodyAccJerk[i].values)    
        fBodyGyro[i] = fast_fourier_transform_one_signal(tBodyGyro[i].values)    

    fBodyAccMag = pd.DataFrame(columns=['fBodyAccMag'])
    fBodyAccMag['fBodyAccMag'] = fast_fourier_transform_one_signal(tBodyAccMag['tBodyAccMag'].values)  

    fBodyAccJerkMag = pd.DataFrame(columns=['fBodyAccJerkMag'])
    fBodyAccJerkMag['fBodyAccJerkMag'] = fast_fourier_transform_one_signal(tBodyAccJerkMag['tBodyAccJerkMag'].values)   

    fBodyGyroMag = pd.DataFrame(columns=['fBodyGyroMag'])
    fBodyGyroMag['fBodyGyroMag'] = fast_fourier_transform_one_signal(tBodyGyroMag['tBodyGyroMag'].values) 

    fBodyGyroJerkMag = pd.DataFrame(columns=['fBodyGyroJerkMag'])
    fBodyGyroJerkMag['fBodyGyroJerkMag'] = fast_fourier_transform_one_signal(tBodyGyroJerkMag['tBodyGyroJerkMag'].values) 

    
    return tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk, \
           tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, \
           fBodyAcc, fBodyAccJerk, fBodyGyro, \
           fBodyAccMag,fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag

        

In [5]:
# Mean Calculation
def mean(x):
    mean_x = np.mean(x)
    return mean_x

# Standard Deviation Calculation
def std_dev(x):
    std_x = np.std(x)
    return std_x

from statsmodels.robust import mad as median_deviation
# Median Absolute Deviation Calculation
def mad(x):
    mad_x = median_deviation(x)
    return mad_x

# Min Calculation
def min_value(x):
    return min(x)

# Max Calculation
def max_value(x):
    return max(x)

from scipy.stats import iqr as IQR
# Inter-quartile range Calculation
def inter_quartile_range(x):
    iqr_x = IQR(x,  axis = 0)
    return iqr_x

# Entropy
from scipy.stats import entropy # import the entropy function
def entropy_axial(x): 
    entropy_vector = entropy(abs(x))
    return entropy_vector

##################################################################################
# 40 FEATURE CALCULATION
##################################################################################

def t_sma_axial(df):
    array=np.array(df)
    sma_axial=float(abs(array).sum())/float(3) # sum of areas under each signal
    return sma_axial # return sma value

# Energy measure. Sum of the squares divided by the number of values. 
def energy_measure(x):
    em_x = np.sum(np.square(x))
    return em_x


def _arburg2(X, order):
    """This version is 10 times faster than arburg, but the output rho is not correct.
    returns [1 a0,a1, an-1]
    """
    x = np.array(X)
    N = len(x)

    if order == 0.:
        raise ValueError("order must be > 0")

    # Initialisation
    # ------ rho, den
    rho = sum(abs(x)**2.) / N  # Eq 8.21 [Marple]_
    den = rho * 2. * N

    # ------ backward and forward errors
    ef = np.zeros(N, dtype=complex)
    eb = np.zeros(N, dtype=complex)
    for j in range(0, N):  # eq 8.11
        ef[j] = x[j]
        eb[j] = x[j]

    # AR order to be stored
    a = np.zeros(1, dtype=complex)
    a[0] = 1
    # ---- rflection coeff to be stored
    ref = np.zeros(order, dtype=complex)

    E = np.zeros(order+1)
    E[0] = rho

    for m in range(0, order):
        # print m
        # Calculate the next order reflection (parcor) coefficient
        efp = ef[1:]
        ebp = eb[0:-1]
        # print efp, ebp
        num = -2. * np.dot(ebp.conj().transpose(), efp)
        den = np.dot(efp.conj().transpose(),  efp)
        den += np.dot(ebp,  ebp.conj().transpose())
        ref[m] = num / den

        # Update the forward and backward prediction errors
        ef = efp + ref[m] * ebp
        eb = ebp + ref[m].conj().transpose() * efp

        # Update the AR coeff.
        a.resize(len(a)+1)
        a = a + ref[m] * np.flipud(a).conjugate()

        # Update the prediction error
        E[m+1] = np.real((1 - ref[m].conj().transpose() * ref[m])) * E[m]
        # print 'REF', ref, num, den
    return a, E[-1], ref

def t_arburg_axial(df):
    # converting signals to 1D numpy arrays for efficiency
    array_X=np.array(df[df.columns[0]])
    array_Y=np.array(df[df.columns[1]])
    array_Z=np.array(df[df.columns[2]])
    
    AR_X = list(_arburg2(array_X,4)[0][1:].real) # list contains real parts of all 4th coefficients generated from signal_X
    AR_Y = list(_arburg2(array_Y,4)[0][1:].real) # list contains real parts of all 4th coefficients generated from signal_Y
    AR_Z = list(_arburg2(array_Z,4)[0][1:].real) # list contains real parts of all 4th coefficients generated from signal_Z
    
    # selecting [AR1 AR2 AR3 AR4] real components for each axis concatenate them in one vector
    AR_vector= AR_X + AR_Y+ AR_Z
    
    # AR_vector contains 12 values 4values per each axis 
    return AR_vector


# correlation(): correlation coefficient between two signals
def coor(signal):
    corr = signal.corr()
    x_y = corr.loc['X','Y']
    x_z = corr.loc['X','Z']
    y_z = corr.loc['Y','Z']
    
    return x_y, x_z, y_z



#################################################################################
# 13 FEATURE
# T VALUES
#################################################################################

# sma: signal magnitude area
def t_sma_mag(mag_column):
    array=np.array(mag_column)
    sma_mag=float(abs(array).sum())# signal magnitude area of one mag column
    return sma_mag

# arburg: auto regression coefficients using the burg method
def t_arburg_mag(mag_column):
    array = np.array(mag_column)    
    AR_vector= list(_arburg2(array,4)[0][1:].real) # AR1, AR2, AR3, AR4 of the mag column
    return AR_vector

##############################################################################
#80 FEATURE EXTRACTION FORMULA 
# FFT RESULTS
##############################################################################
def f_sma_axial(df):
    array=np.array(df)
    sma_value=float((abs(array)/math.sqrt(128)).sum())/float(3) # sma value of 3-axial f_signals
    return sma_value

# energy
def f_energy_axial(x):
    em_x = np.mean(np.square(x))
    return em_x
    
####### Max Inds and Mean_Freq Functions#######################################                                

# max_Inds
def f_max_Inds_axial(df):
    # built frequencies list (each column contain 128 value)
    # duration between each two successive captures is 0.02 s= 1/50hz
    freqs=sp.fftpack.fftfreq(128, d=0.02) 
    array=np.array(df)
    max_Inds_X =freqs[array[1:65,0].argmax()+1] # return the frequency related to max value of f_signal X
    max_Inds_Y =freqs[array[1:65,1].argmax()+1] # return the frequency related to max value of f_signal Y
    max_Inds_Z =freqs[array[1:65,2].argmax()+1] # return the frequency related to max value of f_signal Z
    max_Inds_vector= [max_Inds_X,max_Inds_Y,max_Inds_Z]# put those frequencies in a list
    return max_Inds_vector

# mean freq()
def f_mean_Freq_axial(df):
    # built frequencies list (each column contain 128 value)
    # duration between each two successive captures is 0.02 s= 1/50hz
    freqs=sp.fftpack.fftfreq(128, d=0.02) 
    array=np.array(df)
    
   
    
    # sum of( freq_i * f_signal[i])/ sum of signal[i]
    mean_freq_X = np.dot(freqs,array[:,0]).sum() / float(array[:,0].sum()) #  frequencies weighted sum using f_signalX
    mean_freq_Y = np.dot(freqs,array[:,1]).sum() / float(array[:,1].sum()) #  frequencies weighted sum using f_signalY 
    mean_freq_Z = np.dot(freqs,array[:,2]).sum() / float(array[:,2].sum()) #  frequencies weighted sum using f_signalZ
    mean_freq_vector=[mean_freq_X,mean_freq_Y,mean_freq_Z] # vector contain mean frequencies[X,Y,Z]
    return  mean_freq_vector

# skewness(): skewness of the frequency domain signal 
def skewness(x):
    skew_x=stats.skew(x)
    return skew_x

# kurtosis(): kurtosis of the frequency domain signal 
def kurtosis(x):
    kurt_x = stats.kurtosis(x,fisher=False)
    return kurt_x

def f_one_band_energy(f_signal,band): # f_signal is one column in frequency axial signals in f_window
    # band: is one tuple in B1 ,B2 or B3 
    f_signal_bounded = f_signal[band[0]:band[1]] # select f_signal components included in the band
    energy_value=float((f_signal_bounded**2).sum()/float(len(f_signal_bounded))) # energy value of that band
    return energy_value



######################################################################### 
#Functions used to generate frequency magnitude features
#13 FEATURE
#########################################################################

# sma
def f_sma_mag(mag_column):
    array=np.array(mag_column)
    sma_value=float((abs(array)/math.sqrt(len(mag_column))).sum()) # sma of one mag f_signals
    return sma_value

# energy
def f_energy_mag(mag_column):
    array=np.array(mag_column)
    # spectral energy value
    energy_value=float((array**2).sum()/float(len(array))) # energy value of one mag f_signals
    return energy_value


# Max Inds and Mean_Freq Functions
# max_Inds
def f_max_Inds_mag(mag_column):
    freqs=sp.fftpack.fftfreq(128, d=0.02) 
    array=np.array(mag_column)
    max_Inds_value =float(freqs[array[1:65].argmax()+1]) # freq value related with max component
    return max_Inds_value

# mean freq()
def f_mean_Freq_mag(mag_column):
    freqs=sp.fftpack.fftfreq(128, d=0.02) 
    array=np.array(mag_column)
    mean_freq_value = float(np.dot(freqs,array).sum() / float(array.sum())) # weighted sum of one mag f_signal
    return  mean_freq_value


#Skewness & Kurtosis
from scipy.stats import skew           # skewness
def f_skewness_mag(mag_column):
    array=np.array(mag_column)
    skew_value     = float(skew(array)) # skewness value of one mag f_signal
    return skew_value

from scipy.stats import kurtosis       # kurtosis
def f_kurtosis_mag(mag_column):
    array=np.array(mag_column)
    kurtosis_value = float(kurtosis(array)) # kurotosis value of on mag f_signal
    return kurtosis_value




#################################################################################################
#LAST FEATURES
#ANGLES
############### Angles Functions ####################################
from math import acos # inverse of cosinus function
from math import sqrt # square root function

########Euclidian magnitude 3D############
def magnitude_vector(vector3D): # vector[X,Y,Z]
    return sqrt((vector3D**2).sum()) # eulidian norm of that vector

###########angle between two vectors in radian ###############
def angle(vector1, vector2):
    vector1_mag=magnitude_vector(vector1) # euclidian norm of V1
    vector2_mag=magnitude_vector(vector2) # euclidian norm of V2
   
    scalar_product=np.dot(vector1,vector2) # scalar product of vector 1 and Vector 2
    cos_angle=scalar_product/float(vector1_mag*vector2_mag) # the cosinus value of the angle between V1 and V2
    
    # just in case some values were added automatically
    if cos_angle>1:
        cos_angle=1
    elif cos_angle<-1:
        cos_angle=-1
    
    angle_value=float(acos(cos_angle)) # the angle value in radian
    return angle_value # in radian.





# Feature Collections

In [6]:
def feature_40(signal, name):
    l = [ 'mean_X', 'mean_Y', 'mean_Z',
         'std_X','std_Y', 'std_Z',
         'mad_X','mad_Y', 'mad_Z',
         'max_X','max_Y', 'max_Z',
         'min_X','min_Y', 'min_Z',
         'sma',
         'energy_X', 'energy_Y','energy_Z',
         'iqr_X','iqr_Y','iqr_Z',
         'entropy_X', 'entropy_Y', 'entropy_Z',
         'X_1','X_2','X_3','X_4','Y_1','Y_2','Y_3','Y_4', 'Z_1','Z_2','Z_3','Z_4',
         'correlation_x_y','correlation_x_z', 'correlation_y_z'
         ]
    col = ['X','Y','Z']
    fet_40 = dict()
    
    for i in col:
        fet_40['mean_' + i ] = mean(signal[i])
        fet_40['std_' + i ] = std_dev(signal[i])
        fet_40['mad_' + i ] = mad(signal[i])
        fet_40['max_' + i ] = max_value(signal[i])
        fet_40['min_' + i ] = min_value(signal[i])
        fet_40['energy_' + i ] = energy_measure(signal[i])
        fet_40['iqr_' + i ] = inter_quartile_range(signal[i])
        fet_40['entropy_' + i ] = entropy_axial(signal[i])
    
    
    
    counter = -1
    for count in range(1,13):
        index = 4 if count % 4  == 0 else count % 4 
        counter += 1 if index == 1 else 0
        i = col[counter]  
        
        arCoeff = t_arburg_axial(signal)
        fet_40[i + '_' + str(index)] = arCoeff[count-1]
          

      
        
    fet_40['sma'] = t_sma_axial(signal)
    fet_40['correlation_x_y'] = coor(signal)[0]
    fet_40['correlation_x_z'] = coor(signal)[1]
    fet_40['correlation_y_z'] = coor(signal)[2]
    
    res = {}
    for key in l:
        res[name+'_'+key] = fet_40[key]
    
    return res

def feature_13(signal, name):
    fet_13 = dict()
    
    fet_13[name + '_mean'] = mean(signal)
    fet_13[name + '_std'] = std_dev(signal)
    fet_13[name + '_mad'] = mad(signal)
    fet_13[name + '_max'] = max_value(signal)
    fet_13[name + '_min'] = min_value(signal)
    fet_13[name + '_sma'] = t_sma_mag(signal)
    fet_13[name + '_energy'] = energy_measure(signal)
    fet_13[name + '_iqr'] = inter_quartile_range(signal)
    fet_13[name + '_entropy'] = entropy_axial(signal)
    
    t_arburg= t_arburg_mag(signal)
    for count in range(1,5):
        fet_13[name + '_AR_' + str(count)] = t_arburg[count-1]
    
    return fet_13

def feature_80(signal, name):
    l = ['mean_X', 'mean_Y', 'mean_Z',
         'std_X','std_Y', 'std_Z',
         'mad_X','mad_Y', 'mad_Z',
         'max_X','max_Y', 'max_Z',
         'min_X','min_Y', 'min_Z',
         'sma',
         'energy_X', 'energy_Y','energy_Z',
         'iqr_X', 'iqr_Y', 'iqr_Z',
         'entropy_X', 'entropy_Y', 'entropy_Z',
         'maxInds_X', 'maxInds_Y', 'maxInds_Z',
         'meanFreq_X', 'meanFreq_Y', 'meanFreq_Z',
         'skewness_X', 'kurtosis_X', 'skewness_Y', 'kurtosis_Y', 'skewness_Z', 'kurtosis_Z',
         'bandpower_X-1-8', 'bandpower_X-9-16', 'bandpower_X-17-24', 'bandpower_X-25-32', 'bandpower_X-33-40', 
         'bandpower_X-41-48', 'bandpower_X-49-56', 'bandpower_X-57-64', 
         'bandpower_X-1-16', 'bandpower_X-17-32', 'bandpower_X-33-48', 'bandpower_X-49-64',
         'bandpower_X-1-24', 'bandpower_X-25-48',
         
         'bandpower_Y-1-8', 'bandpower_Y-9-16', 'bandpower_Y-17-24', 'bandpower_Y-25-32', 'bandpower_Y-33-40', 
         'bandpower_Y-41-48', 'bandpower_Y-49-56', 'bandpower_Y-57-64', 
         'bandpower_Y-1-16', 'bandpower_Y-17-32', 'bandpower_Y-33-48', 'bandpower_Y-49-64', 
         'bandpower_Y-1-24', 'bandpower_Y-25-48',
         
         'bandpower_Z-1-8', 'bandpower_Z-9-16', 'bandpower_Z-17-24', 'bandpower_Z-25-32', 'bandpower_Z-33-40', 
         'bandpower_Z-41-48', 'bandpower_Z-49-56', 'bandpower_Z-57-64', 
         'bandpower_Z-1-16', 'bandpower_Z-17-32', 'bandpower_Z-33-48', 'bandpower_Z-49-64', 
         'bandpower_Z-1-24', 'bandpower_Z-25-48' 
         ]

    col = ['X','Y','Z']
    fet_80 = dict()
    
    for i in col:
        fet_80['mean_' + i ] = mean(signal[i])
        fet_80['std_' + i ] = std_dev(signal[i])
        fet_80['mad_' + i ] = mad(signal[i])
        fet_80['max_' + i ] = max_value(signal[i])
        fet_80['min_' + i ] = min_value(signal[i])
        fet_80['energy_' + i ] = f_energy_axial(signal[i])
        fet_80['iqr_' + i ] = inter_quartile_range(signal[i])
        fet_80['entropy_' + i ] = entropy_axial(signal[i])
        
        fet_80['skewness_' + i] = skewness(signal[i])
        fet_80['kurtosis_' + i] = kurtosis(signal[i])

        for j in range(1,65,8):
            fet_80['bandpower_' + i + '-' + str(j) + '-' + str(j+7) ] = f_one_band_energy(signal.values, (j, j+7))
            
        for k in range(1,65,16):
            fet_80['bandpower_' + i + '-' + str(k) + '-' + str(k+15) ] = f_one_band_energy(signal.values, (k, k+15))

        for q in range(1,65,24):
            if q+23 > 65:break
            fet_80['bandpower_' + i + '-' + str(q) + '-' + str(q+23)] = f_one_band_energy(signal.values, (q, q+23))
    
    
    for i in range(3):
        fet_80['maxInds_' + col[i] ] = f_max_Inds_axial(signal)[i]
        fet_80['meanFreq_' + col[i] ] = f_mean_Freq_axial(signal)[i]
    
    fet_80['sma'] = f_sma_axial(signal)

    
    res = {}
    for key in l:
        res[name+'_'+key] = fet_80[key]
    
    return res


def feature_13_MAG(signal, name):
    fet_mag = dict()
    
    fet_mag[name + '_mean'] = mean(signal)
    fet_mag[name + '_std'] = std_dev(signal)
    fet_mag[name + '_mad'] = mad(signal)
    fet_mag[name + '_max'] = max_value(signal)
    fet_mag[name + '_min'] = min_value(signal)
    fet_mag[name + '_sma'] = f_sma_mag(signal)
    fet_mag[name + '_energy'] = f_energy_mag(signal)
    fet_mag[name + '_iqr'] = inter_quartile_range(signal)
    fet_mag[name + '_entropy'] = entropy(signal)
    
    fet_mag[name + '_maxInds' ] = f_max_Inds_mag(signal)
    fet_mag[name + '_meanFreq'] = f_mean_Freq_mag(signal)
    fet_mag[name + '_skewness'] = f_skewness_mag(signal)
    fet_mag[name + '_kurtosis'] = f_kurtosis_mag(signal)    
    
    return fet_mag


def last_features(tGravityAcc,tBodyAcc,tBodyAccJerk,tBodyGyro,tBodyGyroJerk):
    feat = dict()
    
    V2_Vector=np.array(tGravityAcc.mean()) # mean values
    
    # angle 0: angle between (t_body_acc[X.mean,Y.mean,Z.mean], t_gravity[X.mean,Y.mean,Z.mean])
    V1_Vector=np.array(tBodyAcc[col].mean()) # mean values of t_body_acc[X,Y,Z]
    feat['tBodyAccMean_angle'] = angle(V1_Vector, V2_Vector) # angle between the vectors added to the global list
    
    # angle 1: (t_body_acc_jerk[X.mean,Y.mean,Z.mean],t_gravity[X.mean,Y.mean,Z.mean]
    V1_Vector=np.array(tBodyAccJerk[col].mean())
    feat['tBodyAccJerkMean_angle'] = angle(V1_Vector, V2_Vector)
    
    # angle 2: (t_body_gyro[X.mean,Y.mean,Z.mean],t_gravity[X.mean,Y.mean,Z.mean]
    V1_Vector=np.array(tBodyGyro[col].mean())
    feat['tBodyGyroMean_angle'] =  angle(V1_Vector, V2_Vector)
    
    # angle 3: (t_body_gyro_jerk[X.mean,Y.mean,Z.mean],t_gravity[X.mean,Y.mean,Z.mean]
    V1_Vector=np.array(tBodyGyroJerk[col].mean())
    feat['tBodyGyroJerkMean_angle'] = angle(V1_Vector, V2_Vector)
    
    
    # V1 vector in this case is the X axis itself [1,0,0]
    # angle 4: ([X_axis],t_gravity[X.mean,Y.mean,Z.mean])   
    V1_Vector=np.array([1,0,0])
    feat['tGravityAcc_X_angle'] = angle(V1_Vector, V2_Vector)
    
    # V1 vector in this case is the Y axis itself [0,1,0]
    # angle 5: ([Y_acc_axis],t_gravity[X.mean,Y.mean,Z.mean]) 
    V1_Vector=np.array([0,1,0])
    feat['tGravityAcc_Y_angle'] = angle(V1_Vector, V2_Vector)
    
    # V1 vector in this case is the Z axis itself [0,0,1]
    # angle 6: ([Z_acc_axis],t_gravity[X.mean,Y.mean,Z.mean])
    V1_Vector=np.array([0,0,1])
    feat['tGravityAcc_Z_angle'] = angle(V1_Vector, V2_Vector)
    
 
    return feat  

In [7]:
def collectFeatures(tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk,
                    tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, 
                    fBodyAcc, fBodyAccJerk, fBodyGyro, 
                    fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag):
    res = dict()
    
    feat40 = {'tBodyAcc':tBodyAcc,'tGravityAcc': tGravityAcc,'tBodyAccJerk':tBodyAccJerk,
              'tBodyGyro':tBodyGyro,'tBodyGyroJerk': tBodyGyroJerk} 
    for k,v in feat40.items():
        res.update(feature_40(v,k ))
    
    
    
    feat13 = {'tBodyAccMag': tBodyAccMag,'tGravityAccMag': tGravityAccMag,
              'tBodyAccJerkMag': tBodyAccJerkMag,'tBodyGyroMag': tBodyGyroMag,
              'tBodyGyroJerkMag':tBodyGyroJerkMag}
    for k,v in feat13.items():
        res.update(feature_13(v[k],k ))
    
    
    
    feat_80 = {'fBodyAcc': fBodyAcc, 'fBodyAccJerk': fBodyAcc, 'fBodyGyro': fBodyGyro}
    for k,v in feat_80.items():
        res.update(feature_80(v,k))
    
    
    
    feat13_mag = {'fBodyAccMag':fBodyAccMag,'fBodyAccJerkMag': fBodyAccJerkMag,
                  'fBodyGyroMag': fBodyGyroMag, 'fBodyGyroJerkMag': fBodyGyroJerkMag}
    for k,v in feat13_mag.items():
        res.update(feature_13_MAG(v[k],k ))
    
    res.update(last_features(tGravityAcc,tBodyAcc,tBodyAccJerk,tBodyGyro,tBodyGyroJerk))
  
    return res

# TEST

In [8]:
pd.options.display.float_format = '{:,.6f}'.format
pd.options.display.max_columns = 999

In [10]:
col_DF = pd.read_csv('Test_DATASET/test_data.csv').columns
path = 'Real-time_v1'

In [66]:
base_acc = pd.read_csv('UCI HAR Dataset/train/InertialSignals/Acc_all.csv',  delimiter = ',')
base_gryo = pd.read_csv('UCI HAR Dataset/train/InertialSignals/Gyro_all.csv',  delimiter = ',')

print(base_acc.shape, base_gryo.shape)

(941056, 3) (941056, 3)


In [11]:
print(base_acc.shape, base_gryo.shape)

last = pd.DataFrame(columns=col_DF)
print(last.shape)

n = base_acc.shape[0]//128 -1

for i in range(n):
    print(i)
    gryo = base_gryo.iloc[i*128:(i+1) * 129 - i,:]
    acc = base_acc.iloc[i*128:(i+1) * 129 - i ,:]

    result = {}

    tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk, \
    tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, \
    fBodyAcc, fBodyAccJerk, fBodyGyro, \
    fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag = main(gryo,acc)


    result = collectFeatures(tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk,
                             tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, 
                             fBodyAcc, fBodyAccJerk, fBodyGyro, 
                             fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag)
    
    result = pd.DataFrame(result, index=[0])

    last = pd.concat([last, result], axis = 0)




walking_down = last
print(walking_down.shape)
walking_down.describe()

In [53]:
walking_down.to_csv('ACC_NEW_ALL.csv' , index = None)

In [66]:
_,grav_acc,body_acc,_=components_selection_one_signal(base_acc['X']) 

# _,_,body_gyro,_=components_selection_one_signal(med_filtred,freq1,freq2)  # apply components selection
            

In [67]:
grav_acc

array([0.96712626, 0.96739527, 0.96766541, ..., 0.96632583, 0.96659154,
       0.96685835])

In [86]:
base_acc = pd.read_csv('UCI HAR Dataset/test/InertialSignals/acc_test_all.csv',  delimiter = ',')[:1000]
base_gryo = pd.read_csv('UCI HAR Dataset/test/InertialSignals/gyro_test_all.csv',  delimiter = ',')[:1000]

print(base_acc.shape, base_gryo.shape)


print(base_acc.shape, base_gryo.shape)

last = pd.DataFrame(columns=col_DF)
print(last.shape)

n = base_acc.shape[0]//128 -1

for i in range(n):
    print(i)
    gryo = base_gryo.iloc[i*128:(i+1) * 129 - i,:]
    acc = base_acc.iloc[i*128:(i+1) * 129 - i ,:]

    result = {}

    tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk, \
    tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, \
    fBodyAcc, fBodyAccJerk, fBodyGyro, \
    fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag = main(gryo,acc)


    result = collectFeatures()
    result = pd.DataFrame(result, index=[0])

    last = pd.concat([last, result], axis = 0)

#     grav_acc_mag = mag_3_signals(tGravityAcc["X"], tGravityAcc['Y'], tGravityAcc['Z'])

#     print('mean value = '+str(np.array(grav_acc_mag).mean())[0:5]+ ' g')


test_data = last
print(test_data.shape)
test_data.describe()

(1000, 3) (1000, 3)
(1000, 3) (1000, 3)
(0, 561)
0
mean value = 1.038 g
1
mean value = 1.038 g
2
mean value = 1.038 g
3
mean value = 1.039 g
4
mean value = 1.039 g
5
mean value = 1.039 g
(6, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count         6.000000         6.000000         6.000000        6.000000   
mean         -0.008139        -0.012583        -0.001716        0.025958   
std           0.010474         0.026903         0.008348        0.014823   
min          -0.027379        -0.066872        -0.017690        0.014595   
25%          -0.010780        -0.007197        -0.001010        0.016085   
50%          -0.003526        -0.002203         0.000341        0.020562   
75%          -0.001429         0.000621         0.000926        0.029245   
max          -0.000473         0.003078         0.007053        0.053298   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count        6.000000        6.000000        6.000000        6.000000   
mean         0.035751        0.019188        0.021795        0.024999   
std          0.032641        0.009224        0.010654        0.021808   
min          0.014985        0.011998        0.011170        0.010266   
25%          0.016682        0.014935        0.015468        0.014594   
50%          0.018813        0.015998        0.020393        0.016099   
75%          0.041313        0.018335        0.022704        0.022798   
max          0.097109        0.037438        0.041514        0.068409   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count        6.000000        6.000000        6.000000        6.000000   
mean         0.016974        0.057459        0.110509        0.046112   
std          0.004497        0.034125        0.124052        0.015724   
min          0.013064        0.027161        0.014138        0.026171   
25%          0.013964        0.032818        0.023942        0.035694   
50%          0.015717        0.044461        0.044757        0.045835   
75%          0.018013        0.079328        0.202324        0.054134   
max          0.025185        0.108784        0.287550        0.069615   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count        6.000000        6.000000        6.000000      6.000000   
mean        -0.070154       -0.110992       -0.044518      2.805843   
std          0.059572        0.130040        0.046132      2.169871   
min         -0.187582       -0.374377       -0.137466      1.524562   
25%         -0.068827       -0.078374       -0.036180      1.663164   
50%         -0.042102       -0.062267       -0.026210      1.835456   
75%         -0.037410       -0.052215       -0.021262      2.642062   
max         -0.035555       -0.034433       -0.018104      7.122921   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count           6.000000           6.000000           6.000000   
mean            0.129868           0.374718           0.064010   
std             0.168029           0.696247           0.076797   
min             0.027296           0.029956           0.018567   
25%             0.034437           0.036782           0.028644   
50%             0.055752           0.050613           0.036167   
75%             0.129079           0.241773           0.044714   
max             0.459555           1.779462           0.219459   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count        6.000000        6.000000        6.000000            6.000000   
mean         0.029348        0.035436        0.023647            4.569432   
std          0.014221        0.029899        0.005334            0.045834   
min          0.016478        0.014593        0.017863            4.511393   
25%          0.021725        0.018433        0.020209            4.531846   
50%          0.025464        0.023692        0.023038            4.576469   
75%          0.030147        0.036025        0.025054            4.609643   
max          0.056496        0.093820        0.032952            4.614589   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [55]:
test_data.to_csv('TEST_NEW_ALL2.csv' , index = None)

In [92]:
base_acc = pd.read_csv('Real-Time/lying_acc.csv',  delimiter = ',')
# base_gryo = pd.read_csv('UCI HAR Dataset/test/InertialSignals/gyro_test_all.csv',  delimiter = ',')[:1000]

In [94]:
base_acc.describe() 

X            Y            Z
count 1,450.000000 1,450.000000 1,450.000000
mean     -0.284662    -0.543914    10.074603
std       0.050330     0.049801     0.046284
min      -0.600000    -0.770489     9.241082
25%      -0.314656    -0.579362    10.048659
50%      -0.285942    -0.539581    10.074382
75%      -0.257228    -0.508625    10.100105
max      -0.018544    -0.311665    10.259826

In [96]:
lying = pd.read_csv('Real-Time/lying_acc.csv',  delimiter = ',')
walking = pd.read_csv('Real-Time/walking_acc.csv',  delimiter = ',')
sit = pd.read_csv('Real-Time/sitting_acc.csv',  delimiter = ',')
stay = pd.read_csv('Real-Time/staying_acc.csv',  delimiter = ',')
wa = pd.read_csv('Real-Time/walking_up_acc.csv',  delimiter = ',')
wd = pd.read_csv('Real-Time/walking_down_acc.csv',  delimiter = ',')

test_all_acc = pd.concat([lying,walking,sit,stay,wa, wd] , names = col)

In [64]:
lying_gryo = pd.read_csv('Real-Time/lying_gryo.csv',  delimiter = ',')
walking_gryo = pd.read_csv('Real-Time/walking_gryo.csv',  delimiter = ',')
sit_gryo = pd.read_csv('Real-Time/sitting_gryo.csv',  delimiter = ',')
stay_gryo = pd.read_csv('Real-Time/staying_gryo.csv',  delimiter = ',')
wa_gryo = pd.read_csv('Real-Time/walking_up_gryo.csv',  delimiter = ',')
wd_gryo = pd.read_csv('Real-Time/walking_down_gryo.csv',  delimiter = ',')

test_gryo_all = pd.concat([lying_gryo,walking_gryo,sit_gryo,stay_gryo,wa_gryo, wd_gryo] , names = col)

In [65]:
test_gryo_all.describe()#Collected

X            Y            Z
count 8,935.000000 8,935.000000 8,935.000000
mean      0.060392    -0.002872    -0.011733
std       0.296401     0.206226     0.192195
min      -5.004208    -5.004208    -4.712367
25%      -0.016952    -0.023213    -0.067195
50%       0.006109     0.005803    -0.010690
75%       0.079871     0.032376     0.039095
max       5.003444     5.003444     4.232074

In [67]:
base_gryo.describe()

X              Y              Z
count 941,056.000000 941,056.000000 941,056.000000
mean        0.000506      -0.000824       0.000113
std         0.406815       0.381855       0.255743
min        -4.733656      -5.974330      -2.763014
25%        -0.044328      -0.055065      -0.025253
50%         0.000138      -0.000578       0.000490
75%         0.054847       0.036958       0.049530
max         4.155473       5.746062       2.365982

In [104]:
base_acc.describe() #Train

X              Y              Z
count 941,056.000000 941,056.000000 941,056.000000
mean        0.804749       0.028755       0.086498
std         0.414112       0.390996       0.357769
min        -0.466556      -1.582079      -1.639609
25%         0.664948      -0.220610      -0.131162
50%         0.955993      -0.081328       0.039140
75%         1.019197       0.191284       0.238996
max         2.197618       1.217350       1.281363

In [ ]:
print(base_acc.shape, base_gryo.shape)


print(base_acc.shape, base_gryo.shape)

last = pd.DataFrame(columns=col_DF)
print(last.shape)

n = base_acc.shape[0]//128 -1

for i in range(n):
    print(i)
    gryo = base_gryo.iloc[i*128:(i+1) * 129 - i,:]
    acc = base_acc.iloc[i*128:(i+1) * 129 - i ,:]

    result = {}

    tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk, \
    tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, \
    fBodyAcc, fBodyAccJerk, fBodyGyro, \
    fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag = main(gryo,acc)


    result = collectFeatures()
    result = pd.DataFrame(result, index=[0])

    last = pd.concat([last, result], axis = 0)

#     grav_acc_mag = mag_3_signals(tGravityAcc["X"], tGravityAcc['Y'], tGravityAcc['Z'])

#     print('mean value = '+str(np.array(grav_acc_mag).mean())[0:5]+ ' g')


test_data = last
print(test_data.shape)
test_data.describe()

In [ ]:
from sklearn.preprocessing import MinMaxScaler

X_test = test.copy()

scaler = MinMaxScaler(feature_range = [-1,1])
X_test  = scaler.fit_transform(X_test)

result = pd.DataFrame(data = X_test, columns= walking_up.columns)
result.to_csv('Real-Time/X_test.csv', index = None)

mean value = 0.013 g


# Real-Time Data

In [11]:
import warnings
warnings.filterwarnings("ignore")

In [12]:
col_DF = pd.read_csv('Test_DATASET/test_data.csv').columns
path = 'Real-time_v1'

In [13]:
def mag_3_signals(x,y,z): # Euclidian magnitude
    return [math.sqrt((x[i]**2+y[i]**2+z[i]**2)) for i in range(len(x))]

def Processing(path, acc , gyro):
    col = ['X', 'Y', 'Z']
    
    base_acc = pd.read_csv('{0}/{1}'.format(path,acc))
    base_gryo = pd.read_csv('{0}/{1}'.format(path,gyro))

    print(base_acc.shape, base_gryo.shape)

    last = pd.DataFrame(columns=col_DF)
    print(last.shape)

    n = base_acc.shape[0]//128 -1
    for i in range(n):
        gryo = base_gryo.iloc[i*128:(i+1) * 129 - i,:]
        acc = base_acc.iloc[i*128:(i+1) * 129 - i ,:]
        
        
#         for i in col:
#             acc[i] = acc.loc[:, i] / 9.8

        result = {}

        tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk, \
        tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, \
        fBodyAcc, fBodyAccJerk, fBodyGyro, \
        fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag = main(gryo,acc)


        result = collectFeatures(tBodyAcc, tGravityAcc, tBodyAccJerk, tBodyGyro, tBodyGyroJerk,
                                 tBodyAccMag, tGravityAccMag,tBodyAccJerkMag, tBodyGyroMag, tBodyGyroJerkMag, 
                                 fBodyAcc, fBodyAccJerk, fBodyGyro, 
                                 fBodyAccMag, fBodyAccJerkMag, fBodyGyroMag,fBodyGyroJerkMag)
        result = pd.DataFrame(result, index=[0])
        
#         grav_acc_mag = mag_3_signals(tGravityAcc["X"], tGravityAcc['Y'], tGravityAcc['Z'])

#         print('mean value = '+str(np.array(grav_acc_mag).mean())[0:5]+ ' g')


        last = pd.concat([last, result], axis = 0)


    return last

# Walking

In [14]:
walking = Processing(path, 'walking_acc.csv','walking_gryo.csv')
walking.describe()

(5908, 3) (5908, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        45.000000        45.000000        45.000000       45.000000   
mean          0.000433        -0.025936        -0.003121        0.341665   
std           0.073022         0.087512         0.023588        0.042196   
min          -0.185721        -0.298416        -0.057967        0.256403   
25%          -0.039031        -0.070166        -0.015231        0.309169   
50%          -0.015543        -0.009747        -0.002135        0.344971   
75%           0.043652         0.029903         0.011588        0.373353   
max           0.163316         0.160842         0.051733        0.432595   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.375363        0.142288        0.315604        0.281418   
std          0.070948        0.019172        0.061745        0.075225   
min          0.266846        0.110989        0.196680        0.163138   
25%          0.332975        0.129542        0.268976        0.235476   
50%          0.371921        0.138994        0.314837        0.262628   
75%          0.400838        0.152156        0.358037        0.329922   
max          0.586681        0.191085        0.451711        0.508833   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.140572        0.734213        1.090035        0.316753   
std          0.025410        0.195116        0.256427        0.078732   
min          0.088135        0.438202        0.476699        0.185932   
25%          0.122636        0.595122        0.954946        0.269265   
50%          0.143261        0.711468        1.098386        0.306901   
75%          0.156643        0.849581        1.237803        0.350483   
max          0.199404        1.174440        1.557288        0.546322   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       45.000000       45.000000       45.000000     45.000000   
mean        -0.854294       -1.128276       -0.337588     28.462927   
std          0.142794        0.361656        0.065065      3.769420   
min         -1.209561       -2.217856       -0.532873     22.053530   
25%         -0.945205       -1.339468       -0.384079     25.754483   
50%         -0.837778       -1.016868       -0.335326     27.827522   
75%         -0.755290       -0.911736       -0.286188     30.669957   
max         -0.572608       -0.545399       -0.231084     39.968930   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          45.000000          45.000000          45.000000   
mean           15.832259          19.709450           2.708350   
std             4.278288           9.217575           0.770617   
min             8.548351           9.140287           1.594658   
25%            12.263816          14.502197           2.161131   
50%            15.355017          18.971122           2.474694   
75%            19.048079          21.893895           3.022808   
max            27.367776          55.455634           4.707559   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       45.000000       45.000000       45.000000           45.000000   
mean         0.421742        0.379992        0.188286            4.539015   
std          0.080023        0.101882        0.036710            0.058688   
min          0.281768        0.217166        0.118225            4.404903   
25%          0.367056        0.307864        0.164816            4.504820   
50%          0.406897        0.367278        0.185430            4.533768   
75%          0.476194        0.427060        0.209965            4.571883   
max          0.633568        0.691055        0.271064            4.681459   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [15]:
walking_up1 = Processing(path, 'walking_up_acc1.csv','walking_up_gryo1.csv')
walking_up1.describe()

(2253, 3) (2253, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        16.000000        16.000000        16.000000       16.000000   
mean         -0.011963        -0.008461        -0.000405        0.215329   
std           0.037774         0.058809         0.019830        0.038726   
min          -0.072294        -0.123146        -0.039356        0.154151   
25%          -0.037720        -0.029421        -0.014118        0.192377   
50%          -0.010299        -0.008323         0.000285        0.211880   
75%           0.013537         0.024345         0.011335        0.240669   
max           0.069604         0.096381         0.043215        0.279352   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.286748        0.108853        0.189731        0.262694   
std          0.062592        0.021561        0.035615        0.048910   
min          0.206152        0.076142        0.143690        0.180938   
25%          0.252805        0.092274        0.164314        0.234015   
50%          0.267366        0.105453        0.183209        0.273057   
75%          0.295535        0.123547        0.201545        0.301055   
max          0.441919        0.143399        0.279725        0.344307   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.103795        0.477297        0.689395        0.284145   
std          0.020743        0.119491        0.235441        0.093959   
min          0.069564        0.283034        0.449346        0.171576   
25%          0.088481        0.397872        0.535481        0.210282   
50%          0.105426        0.471976        0.646409        0.281542   
75%          0.114657        0.537424        0.787509        0.320940   
max          0.142265        0.725981        1.320862        0.514769   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       16.000000       16.000000       16.000000     16.000000   
mean        -0.547947       -0.709553       -0.240876     20.633322   
std          0.142713        0.251377        0.071297      2.932141   
min         -0.782482       -1.334350       -0.378970     16.020194   
25%         -0.653958       -0.764388       -0.275295     18.707668   
50%         -0.529884       -0.620236       -0.245707     20.558660   
75%         -0.448465       -0.570228       -0.179883     22.608450   
max         -0.360511       -0.462450       -0.126418     26.411433   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          16.000000          16.000000          16.000000   
mean            6.304422          11.419004           1.619664   
std             2.297636           5.638904           0.596790   
min             3.044345           5.724660           0.752455   
25%             4.815217           8.876459           1.121995   
50%             5.788763           9.355798           1.563904   
75%             7.806436          11.472008           1.971751   
max            10.657790          26.917369           2.636826   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       16.000000       16.000000       16.000000           16.000000   
mean         0.255226        0.362284        0.139412            4.531614   
std          0.053237        0.061772        0.027266            0.048716   
min          0.187255        0.248055        0.096377            4.417213   
25%          0.214978        0.325625        0.118803            4.503656   
50%          0.246581        0.368987        0.143586            4.529781   
75%          0.280693        0.408450        0.152681            4.565307   
max          0.388499        0.477310        0.190039            4.609268   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [16]:
walking_up2 = Processing(path, 'walking_up_acc2.csv','walking_up_gryo2.csv')
walking_up2.describe()

(2253, 3) (2253, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        16.000000        16.000000        16.000000       16.000000   
mean         -0.010492         0.010220         0.002214        0.237994   
std           0.041266         0.057185         0.018704        0.053829   
min          -0.072364        -0.082931        -0.031758        0.159473   
25%          -0.029943        -0.036209        -0.008157        0.196860   
50%          -0.016316         0.022830         0.000074        0.234874   
75%           0.006832         0.054117         0.013091        0.249678   
max           0.089368         0.093505         0.043896        0.375961   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.323851        0.120260        0.228959        0.309016   
std          0.053449        0.025613        0.052930        0.067196   
min          0.239506        0.076215        0.144886        0.218801   
25%          0.286719        0.105243        0.186935        0.260376   
50%          0.317124        0.119474        0.233083        0.293274   
75%          0.367561        0.136800        0.282271        0.366469   
max          0.422115        0.167864        0.295147        0.421319   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.112596        0.513357        0.681919        0.335752   
std          0.030639        0.148466        0.157051        0.096641   
min          0.077798        0.329890        0.362832        0.174838   
25%          0.089223        0.415347        0.576439        0.288569   
50%          0.102955        0.472683        0.693406        0.339489   
75%          0.121639        0.562217        0.807203        0.396682   
max          0.180036        0.891698        0.925242        0.528426   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       16.000000       16.000000       16.000000     16.000000   
mean        -0.563975       -0.839466       -0.256637     23.512345   
std          0.188143        0.283346        0.074196      3.603695   
min         -1.013829       -1.569406       -0.451488     17.957870   
25%         -0.609688       -0.905778       -0.288777     20.257188   
50%         -0.524377       -0.778771       -0.248907     23.769838   
75%         -0.449600       -0.648944       -0.211948     25.627949   
max         -0.354340       -0.548284       -0.168963     29.263119   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          16.000000          16.000000          16.000000   
mean            7.816209          14.173143           1.972511   
std             3.719130           4.501472           0.836564   
min             3.525655           7.440271           0.743536   
25%             5.010268          11.125209           1.474551   
50%             7.065045          13.385850           1.850298   
75%             8.587892          17.458326           2.417633   
max            18.472416          22.848775           3.607619   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       16.000000       16.000000       16.000000           16.000000   
mean         0.319427        0.436470        0.152134            4.566473   
std          0.073286        0.094351        0.037744            0.079244   
min          0.191096        0.297084        0.103127            4.339760   
25%          0.258253        0.377522        0.126824            4.560207   
50%          0.325235        0.402303        0.141845            4.583607   
75%          0.386514        0.546960        0.166286            4.614219   
max          0.417945        0.579911        0.241538            4.645906   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [17]:
walking_up3 = Processing(path, 'walking_up_acc3.csv','walking_up_gryo3.csv')
walking_up3.describe()

(2255, 3) (2254, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        16.000000        16.000000        16.000000       16.000000   
mean          0.020068         0.018483         0.006830        0.287120   
std           0.034719         0.066233         0.020926        0.049333   
min          -0.032941        -0.121340        -0.049303        0.181238   
25%          -0.006087        -0.022520         0.000440        0.261072   
50%           0.022314         0.049033         0.009448        0.279074   
75%           0.041602         0.062538         0.014661        0.319415   
max           0.089301         0.115283         0.035335        0.392645   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.315208        0.130703        0.257567        0.314581   
std          0.028623        0.020377        0.061489        0.045734   
min          0.257682        0.097513        0.156389        0.241268   
25%          0.296380        0.118407        0.211404        0.279827   
50%          0.317822        0.129113        0.253086        0.316187   
75%          0.331454        0.141282        0.306026        0.352371   
max          0.363381        0.182900        0.374675        0.398621   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       16.000000       16.000000       16.000000       16.000000   
mean         0.122081        0.665370        0.713196        0.345624   
std          0.027076        0.146123        0.103116        0.071874   
min          0.075718        0.370139        0.471615        0.256677   
25%          0.099543        0.607734        0.665295        0.289448   
50%          0.130356        0.656248        0.708388        0.334797   
75%          0.145994        0.764306        0.789510        0.364418   
max          0.156219        0.874582        0.850507        0.516059   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       16.000000       16.000000       16.000000     16.000000   
mean        -0.681860       -0.686429       -0.263910     25.290068   
std          0.139859        0.118474        0.060801      2.705358   
min         -0.925093       -0.910749       -0.406165     20.875511   
25%         -0.795163       -0.770789       -0.297870     23.288130   
50%         -0.682963       -0.701030       -0.248183     25.362551   
75%         -0.563360       -0.601179       -0.219887     27.113938   
max         -0.405342       -0.477920       -0.172913     31.560223   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          16.000000          16.000000          16.000000   
mean           11.040326          13.386026           2.295018   
std             3.688582           2.461265           0.735323   
min             4.265089           8.502349           1.227935   
25%             8.993215          12.378123           1.814306   
50%            10.161950          13.215871           2.259518   
75%            13.168601          14.272085           2.599387   
max            19.976231          18.786494           4.285360   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       16.000000       16.000000       16.000000           16.000000   
mean         0.356956        0.427195        0.167717            4.542370   
std          0.096796        0.060782        0.040553            0.050201   
min          0.227892        0.344048        0.100156            4.418088   
25%          0.282725        0.377594        0.142349            4.515982   
50%          0.343811        0.413194        0.173884            4.542355   
75%          0.406919        0.475097        0.197297            4.574662   
max          0.565060        0.556248        0.227408            4.611105   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [19]:
walking_down1 = Processing(path, 'walking_down_acc1.csv','walking_down_gryo1.csv')
walking_down1.describe()

(1691, 3) (1691, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        12.000000        12.000000        12.000000       12.000000   
mean          0.015693        -0.037527         0.009494        0.247380   
std           0.052436         0.059127         0.017090        0.037608   
min          -0.132503        -0.125475        -0.020783        0.193617   
25%           0.012559        -0.081032        -0.002138        0.213966   
50%           0.020278        -0.052505         0.009876        0.253398   
75%           0.047040         0.015741         0.017727        0.271556   
max           0.067783         0.053912         0.044508        0.301238   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.396724        0.126505        0.245035        0.335464   
std          0.069777        0.018852        0.043136        0.065752   
min          0.304117        0.097624        0.163625        0.232510   
25%          0.332110        0.112256        0.223872        0.311853   
50%          0.399789        0.130913        0.250652        0.331822   
75%          0.458982        0.141064        0.266160        0.350247   
max          0.494576        0.152774        0.311176        0.504725   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.119139        0.607361        0.957575        0.293004   
std          0.022056        0.152882        0.319637        0.078364   
min          0.081635        0.389159        0.591178        0.181126   
25%          0.102257        0.463532        0.670892        0.227473   
50%          0.118686        0.617799        0.907053        0.279865   
75%          0.138751        0.743153        1.172385        0.341027   
max          0.148916        0.821480        1.424638        0.425356   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       12.000000       12.000000       12.000000     12.000000   
mean        -0.554171       -1.175229       -0.316634     25.782406   
std          0.199565        0.283665        0.071735      2.747621   
min         -1.122335       -1.600072       -0.455050     21.882422   
25%         -0.580907       -1.392817       -0.344494     23.828005   
50%         -0.505062       -1.183284       -0.323036     25.131342   
75%         -0.460232       -0.942934       -0.277925     28.106360   
max         -0.368604       -0.737269       -0.177391     30.385152   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          12.000000          12.000000          12.000000   
mean            8.353299          21.307600           2.135960   
std             2.722102           7.186954           0.637784   
min             4.897556          12.575409           1.223697   
25%             5.900650          14.783170           1.619192   
50%             8.407397          21.186217           2.233530   
75%             9.520300          27.110002           2.607094   
max            13.456229          33.324768           3.241084   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       12.000000       12.000000       12.000000           12.000000   
mean         0.328623        0.464947        0.165122            4.561243   
std          0.056780        0.094557        0.032756            0.053214   
min          0.227652        0.314344        0.121866            4.452630   
25%          0.300446        0.426599        0.133644            4.520956   
50%          0.326560        0.456508        0.165082            4.570052   
75%          0.351630        0.488154        0.197456            4.600037   
max          0.440552        0.666437        0.215763            4.634293   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [20]:
walking_down2 = Processing(path, 'walking_down_acc2.csv','walking_down_gryo2.csv')
walking_down2.describe()

(1692, 3) (1690, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        12.000000        12.000000        12.000000       12.000000   
mean          0.008939        -0.028796        -0.012019        0.260375   
std           0.081406         0.067798         0.022673        0.039497   
min          -0.123230        -0.145343        -0.040792        0.180443   
25%          -0.044542        -0.084882        -0.027720        0.241520   
50%          -0.009675        -0.018872        -0.019682        0.261257   
75%           0.069544         0.008144         0.008091        0.291956   
max           0.164005         0.102050         0.023491        0.321610   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.393374        0.120567        0.239708        0.287582   
std          0.072385        0.023383        0.054651        0.067721   
min          0.302984        0.087912        0.161546        0.204639   
25%          0.361734        0.106246        0.178674        0.248033   
50%          0.370335        0.115323        0.249118        0.274518   
75%          0.406429        0.138508        0.275281        0.306365   
max          0.583746        0.168762        0.330463        0.448018   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.121727        0.563565        0.931327        0.248272   
std          0.029521        0.186007        0.224577        0.072898   
min          0.077045        0.313057        0.677404        0.121392   
25%          0.102554        0.443114        0.742323        0.201387   
50%          0.120829        0.539007        0.947555        0.232377   
75%          0.134941        0.647175        1.075455        0.299958   
max          0.172692        0.988859        1.415522        0.373033   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       12.000000       12.000000       12.000000     12.000000   
mean        -0.642181       -1.237673       -0.315475     25.781695   
std          0.129177        0.425601        0.085474      2.779168   
min         -0.858104       -2.140431       -0.549640     21.857385   
25%         -0.720924       -1.404245       -0.336261     23.565165   
50%         -0.661796       -1.233546       -0.298653     26.462204   
75%         -0.525958       -0.853175       -0.267843     27.557462   
max         -0.440612       -0.750237       -0.220377     30.810079   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          12.000000          12.000000          12.000000   
mean            9.648643          21.067384           2.003608   
std             3.276892           8.317693           0.821841   
min             4.171510          11.876799           1.051832   
25%             7.832537          16.798365           1.494077   
50%             9.362737          18.742924           1.744289   
75%            11.960693          21.839482           2.595782   
max            16.682325          43.771501           3.858521   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       12.000000       12.000000       12.000000           12.000000   
mean         0.332856        0.395703        0.164948            4.565664   
std          0.074010        0.090033        0.043303            0.058234   
min          0.237556        0.251462        0.104961            4.459745   
25%          0.272874        0.352220        0.128042            4.541038   
50%          0.325369        0.377457        0.166200            4.572414   
75%          0.376218        0.416047        0.189101            4.594431   
max          0.488376        0.604293        0.245648            4.658071   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [21]:
walking_down3 = Processing(path, 'walking_down_acc3.csv','walking_down_gryo3.csv')
walking_down3.describe()

(1689, 3) (1689, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        12.000000        12.000000        12.000000       12.000000   
mean          0.002565        -0.030240        -0.013071        0.275049   
std           0.063910         0.074014         0.039982        0.038770   
min          -0.086567        -0.167205        -0.102066        0.212367   
25%          -0.046322        -0.077003        -0.030969        0.255419   
50%          -0.022723        -0.021058        -0.010334        0.274654   
75%           0.044969         0.011514         0.007708        0.291929   
max           0.107663         0.105639         0.049271        0.359370   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.469732        0.145980        0.249770        0.391313   
std          0.102816        0.022272        0.047840        0.106530   
min          0.302424        0.116526        0.189359        0.206929   
25%          0.388090        0.133221        0.212973        0.327054   
50%          0.493541        0.143718        0.240326        0.366395   
75%          0.521411        0.157041        0.275141        0.485495   
max          0.627906        0.196993        0.331823        0.562231   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       12.000000       12.000000       12.000000       12.000000   
mean         0.136367        0.660856        1.014950        0.315356   
std          0.025236        0.145740        0.241006        0.067581   
min          0.099892        0.389312        0.684718        0.223788   
25%          0.120904        0.579267        0.843557        0.274534   
50%          0.130696        0.651214        1.006748        0.307717   
75%          0.144706        0.729565        1.130776        0.333964   
max          0.184084        0.936979        1.476424        0.455361   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       12.000000       12.000000       12.000000     12.000000   
mean        -0.671760       -1.485646       -0.398567     29.545031   
std          0.173206        0.590978        0.139711      3.927940   
min         -0.895781       -2.757400       -0.623537     22.579485   
25%         -0.796532       -1.639994       -0.532950     27.156897   
50%         -0.671519       -1.380139       -0.344755     30.257854   
75%         -0.571925       -1.254663       -0.279765     32.668021   
max         -0.370202       -0.648545       -0.237675     34.050860   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          12.000000          12.000000          12.000000   
mean           10.339919          30.243087           2.995349   
std             3.206513          12.597102           1.216804   
min             5.806116          11.966889           1.808408   
25%             8.616896          20.417992           2.277658   
50%             9.721987          31.780339           2.762054   
75%            11.915796          34.930705           3.304933   
max            17.871416          51.488123           6.300611   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       12.000000       12.000000       12.000000           12.000000   
mean         0.341953        0.523859        0.188409            4.538465   
std          0.059385        0.128724        0.030414            0.058850   
min          0.260404        0.277570        0.138817            4.423759   
25%          0.309629        0.439026        0.173317            4.512113   
50%          0.320406        0.512038        0.181346            4.550352   
75%          0.387559        0.626939        0.195856            4.577852   
max          0.442320        0.725563        0.241869            4.619593   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [22]:
sitting = Processing(path, 'sitting_acc.csv','sitting_gryo.csv')
sitting.describe()

(5934, 3) (5932, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        45.000000        45.000000        45.000000       45.000000   
mean          0.000176        -0.000901        -0.000346        0.007632   
std           0.002475         0.007223         0.001321        0.004151   
min          -0.013581        -0.017949        -0.005224        0.003754   
25%          -0.000476        -0.004426        -0.000960        0.004821   
50%           0.000579        -0.000239        -0.000181        0.006361   
75%           0.001652         0.001669         0.000252        0.007984   
max           0.002336         0.033455         0.002917        0.020171   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.022498        0.004382        0.006496        0.018502   
std          0.018542        0.003463        0.003265        0.015483   
min          0.007029        0.001789        0.002961        0.006062   
25%          0.009752        0.002549        0.004500        0.008742   
50%          0.014131        0.003008        0.005725        0.011258   
75%          0.028216        0.004228        0.006958        0.022786   
max          0.074948        0.017367        0.017361        0.072876   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.003587        0.022532        0.055710        0.010207   
std          0.002494        0.015690        0.055540        0.008906   
min          0.001600        0.007082        0.015559        0.003651   
25%          0.002002        0.013804        0.024767        0.005501   
50%          0.002909        0.017299        0.031172        0.007405   
75%          0.003534        0.022926        0.051760        0.009921   
max          0.013059        0.089122        0.261550        0.050101   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       45.000000       45.000000       45.000000     45.000000   
mean        -0.018846       -0.065587       -0.013817      1.118588   
std          0.014878        0.065702        0.013007      0.815785   
min         -0.075041       -0.355355       -0.065085      0.460435   
25%         -0.017980       -0.073626       -0.014072      0.571255   
50%         -0.013040       -0.037835       -0.008671      0.758209   
75%         -0.011447       -0.028452       -0.006408      1.369698   
max         -0.005087       -0.016868       -0.002883      3.694174   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          45.000000          45.000000          45.000000   
mean            0.010383           0.114449           0.004192   
std             0.013401           0.196181           0.007932   
min             0.001887           0.006808           0.000423   
25%             0.003002           0.013230           0.000883   
50%             0.005496           0.027489           0.001383   
75%             0.008449           0.102756           0.002462   
max             0.057316           0.862262           0.042100   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       45.000000       45.000000       45.000000           45.000000   
mean         0.008855        0.025533        0.004857            4.513424   
std          0.004439        0.021355        0.003355            0.100058   
min          0.003910        0.008171        0.002246            4.022935   
25%          0.006400        0.011984        0.002666            4.471850   
50%          0.007609        0.015173        0.003906            4.530888   
75%          0.009470        0.029299        0.004921            4.562837   
max          0.024069        0.097118        0.017591            4.636836   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [23]:
staying = Processing(path, 'staying_acc.csv','staying_gryo.csv')
staying.describe()

(5928, 3) (5928, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        45.000000        45.000000        45.000000       45.000000   
mean          0.000020         0.000822        -0.000307        0.016653   
std           0.003726         0.005172         0.001182        0.009359   
min          -0.008464        -0.009591        -0.003046        0.007763   
25%          -0.001819        -0.001843        -0.001157        0.011801   
50%          -0.000080         0.000138        -0.000404        0.013853   
75%           0.001975         0.002084         0.000296        0.017777   
max           0.013290         0.019755         0.002630        0.048959   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.018389        0.005584        0.015596        0.016315   
std          0.007923        0.003385        0.008090        0.007048   
min          0.009536        0.002394        0.006745        0.008872   
25%          0.013500        0.003551        0.010895        0.012191   
50%          0.015729        0.004584        0.013645        0.014231   
75%          0.018819        0.005482        0.016571        0.017554   
max          0.041788        0.019170        0.044323        0.042153   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.005017        0.039813        0.051359        0.014366   
std          0.003272        0.025397        0.025954        0.010395   
min          0.002090        0.016477        0.026949        0.004456   
25%          0.003156        0.023036        0.034648        0.007750   
50%          0.004105        0.031321        0.043173        0.009970   
75%          0.005047        0.047344        0.048924        0.017131   
max          0.019123        0.128756        0.149959        0.052913   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       45.000000       45.000000       45.000000     45.000000   
mean        -0.043063       -0.047372       -0.014772      1.373857   
std          0.025037        0.022381        0.008225      0.676636   
min         -0.133358       -0.149726       -0.040075      0.688010   
25%         -0.051176       -0.052468       -0.016433      1.006101   
50%         -0.040502       -0.043653       -0.011892      1.162412   
75%         -0.026029       -0.035379       -0.010175      1.458012   
max         -0.016979       -0.023235       -0.005528      3.698462   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          45.000000          45.000000          45.000000   
mean            0.048198           0.054576           0.005612   
std             0.068240           0.059669           0.008342   
min             0.007968           0.013027           0.000743   
25%             0.017946           0.026154           0.001666   
50%             0.028560           0.031670           0.002967   
75%             0.042337           0.045677           0.004361   
max             0.329418           0.273476           0.047263   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       45.000000       45.000000       45.000000           45.000000   
mean         0.020941        0.022071        0.006737            4.550913   
std          0.010936        0.009804        0.004333            0.058203   
min          0.008343        0.012639        0.002717            4.370305   
25%          0.015058        0.016121        0.004353            4.515641   
50%          0.017827        0.019419        0.005750            4.551778   
75%          0.022832        0.023214        0.006750            4.589667   
max          0.061951        0.058786        0.024949            4.667127   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [24]:
lying = Processing(path, 'lying_acc.csv','lying_gryo.csv')
lying.describe()

(5936, 3) (5936, 3)
(0, 561)


tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
count        45.000000        45.000000        45.000000       45.000000   
mean          0.000439         0.000833        -0.000143        0.002040   
std           0.000487         0.001842         0.001003        0.001289   
min          -0.000555        -0.005043        -0.004133        0.001415   
25%           0.000114         0.000389        -0.000337        0.001624   
50%           0.000504         0.000972        -0.000139        0.001792   
75%           0.000787         0.001643         0.000041        0.001924   
max           0.001831         0.006159         0.002559        0.010105   

       tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.008157        0.003395        0.001784        0.007377   
std          0.009930        0.004838        0.000360        0.008104   
min          0.003059        0.000757        0.001254        0.002642   
25%          0.004254        0.001185        0.001529        0.003757   
50%          0.005508        0.001733        0.001769        0.005383   
75%          0.007842        0.002833        0.001903        0.007000   
max          0.063281        0.023404        0.003019        0.052545   

       tBodyAcc_mad_Z  tBodyAcc_max_X  tBodyAcc_max_Y  tBodyAcc_max_Z  \
count       45.000000       45.000000       45.000000       45.000000   
mean         0.002286        0.007063        0.022341        0.008292   
std          0.003175        0.010587        0.024544        0.009581   
min          0.000763        0.003119        0.005981        0.001466   
25%          0.001065        0.004243        0.011384        0.002979   
50%          0.001304        0.005447        0.014694        0.004985   
75%          0.001577        0.006637        0.021772        0.010194   
max          0.018075        0.075706        0.143009        0.055384   

       tBodyAcc_min_X  tBodyAcc_min_Y  tBodyAcc_min_Z  tBodyAcc_sma  \
count       45.000000       45.000000       45.000000     45.000000   
mean        -0.004541       -0.022207       -0.012365      0.442271   
std          0.002421        0.043353        0.019816      0.451075   
min         -0.016141       -0.296995       -0.109282      0.200882   
25%         -0.005246       -0.018292       -0.012010      0.254296   
50%         -0.004088       -0.013186       -0.005651      0.319372   
75%         -0.003051       -0.009711       -0.003147      0.423678   
max         -0.002176       -0.005561       -0.001866      2.808573   

       tBodyAcc_energy_X  tBodyAcc_energy_Y  tBodyAcc_energy_Z  \
count          45.000000          45.000000          45.000000   
mean            0.000795           0.021373           0.004532   
std             0.001954           0.079099           0.013918   
min             0.000264           0.001322           0.000073   
25%             0.000367           0.002471           0.000180   
50%             0.000455           0.004193           0.000423   
75%             0.000553           0.008960           0.001238   
max             0.013499           0.515826           0.072297   

       tBodyAcc_iqr_X  tBodyAcc_iqr_Y  tBodyAcc_iqr_Z  tBodyAcc_entropy_X  \
count       45.000000       45.000000       45.000000           45.000000   
mean         0.002407        0.009981        0.003187            4.529119   
std          0.000507        0.011214        0.004548            0.109591   
min          0.001754        0.003520        0.001070            3.884974   
25%          0.002000        0.004861        0.001436            4.516812   
50%          0.002312        0.007129        0.001767            4.546076   
75%          0.002681        0.010490        0.002287            4.571896   
max          0.003987        0.072708        0.025981            4.642856   

       tBodyAcc_entropy_Y  tBodyAcc_entropy_Z  tBodyAcc_X_1  tBodyAcc_X_2  \


In [26]:
walking_up = pd.concat([walking_up1,walking_up2,walking_up3],axis = 0)
walking_down = pd.concat([walking_down1, walking_down2, walking_down3],axis = 0)

In [27]:
X = pd.concat([walking, walking_up, walking_down, sitting, staying, lying],axis = 0)

In [31]:
w = [1 for _ in range(walking.shape[0]) ]
up = [2 for _ in range(walking_up.shape[0]) ]
down = [3 for _ in range(walking_down.shape[0]) ]
sit = [4 for _ in range(sitting.shape[0]) ]
s = [5 for _ in range(staying.shape[0]) ]
lay = [6 for _ in range(lying.shape[0]) ]


Y =  w + up + down + sit + s + lay 
Y = pd.DataFrame(data = Y,columns=['Label'])

In [32]:
X.to_csv('{0}/X.csv'.format(path), index = None)
Y.to_csv('{0}/y.csv'.format(path), index = None)

In [29]:
walking_up

tBodyAcc_mean_X  tBodyAcc_mean_Y  tBodyAcc_mean_Z  tBodyAcc_std_X  \
0        -0.013537        -0.009597        -0.008877        0.235351   
0        -0.031212        -0.123146        -0.016841        0.173826   
0        -0.063475         0.075075        -0.021226        0.238241   
0         0.004330         0.042005         0.017302        0.199732   
0        -0.055015        -0.000430         0.015131        0.272541   
0        -0.010344         0.024015        -0.006075        0.247954   
0         0.024931        -0.007048         0.010362        0.197145   
0         0.017374         0.025338         0.006645        0.178073   
0        -0.034084        -0.021666        -0.039356        0.156735   
0        -0.048629         0.096381         0.011007        0.261649   
0        -0.072294        -0.028669        -0.006148        0.279352   
0         0.012257        -0.047172         0.008997        0.206542   
0        -0.004639        -0.014722        -0.019719        0.154151   
0         0.023585        -0.031674         0.012321        0.210852   
0         0.069604        -0.122473         0.043215        0.220211   
0        -0.010254         0.008410        -0.013211        0.212907   
0        -0.007550        -0.033770        -0.015066        0.184464   
0        -0.022350         0.049866         0.014095        0.197714   
0        -0.010986         0.027641         0.000203        0.191514   
0         0.089368         0.018020         0.034384        0.240283   
0        -0.057319        -0.041843        -0.031758        0.223817   
0         0.006881         0.079812         0.000310        0.194299   
0        -0.024603         0.062801        -0.007352        0.246020   
0        -0.045962         0.032616        -0.004922        0.159473   
0         0.006816        -0.065675        -0.006894        0.236483   
0         0.002890        -0.082931        -0.010570        0.233264   
0        -0.022727         0.093505        -0.011613        0.238070   
0        -0.054488         0.051222         0.015527        0.375961   
0         0.009037        -0.034332         0.002488        0.298404   
0         0.057126         0.079814         0.043896        0.260654   
0        -0.072364        -0.029841         0.012757        0.219463   
0        -0.021647        -0.043385        -0.000055        0.308018   
0         0.070598        -0.054844         0.035335        0.300715   
0         0.089301        -0.032741         0.009338        0.269179   
0        -0.014209        -0.018304        -0.026090        0.271203   
0         0.026893         0.053214         0.009557        0.278261   
0         0.035427         0.090208         0.009191        0.244196   
0         0.047197         0.115283         0.025440        0.262977   
0         0.021765         0.055656         0.018172        0.181238   
0         0.040960         0.070336         0.011761        0.255357   
0        -0.019793         0.060743        -0.000874        0.285704   
0        -0.032941         0.056156        -0.000310        0.315847   
0         0.022863         0.004943         0.034542        0.341520   
0        -0.002562        -0.019113         0.000690        0.330119   
0         0.043525         0.067922         0.013490        0.392645   
0        -0.025558         0.044853        -0.049303        0.338041   
0         0.020995        -0.077250         0.005200        0.247038   
0        -0.003380        -0.121340         0.013142        0.279887   

   tBodyAcc_std_Y  tBodyAcc_std_Z  tBodyAcc_mad_X  tBodyAcc_mad_Y  \
0        0.236939        0.136876        0.172868        0.188029   
0        0.299704        0.092666        0.179592        0.281198   
0        0.282621        0.097135        0.205532        0.274248   
0        0.267036        0.100200        0.158349        0.274592   
0        0.252863        0.119834        0.279725        0.305321   
0        0.419577        0.143399        0.237629        0.3